In [0]:
dbutils.fs.mount(
  source = "wasbs://imec@imec.blob.core.windows.net/",
  mount_point = "/mnt/imec",
  extra_configs = {"fs.azure.account.key.imec.blob.core.windows.net":"IUF5U0VO8Fd/X9IqM7o5Rys63kSBJaTlnCDDLtL6xbFN4OA/Fj3Q6S4LwvzCNlFi6K89JuvWaJBV+AStpqCErA=="})

---------------------------------------------------------------------------
ExecutionError                            Traceback (most recent call last)
File <command-4150418451625901>:1
----> 1 dbutils.fs.mount(
      2   source = "wasbs://imec@imec.blob.core.windows.net/",
      3   mount_point = "/mnt/imec",
      4   extra_configs = {"fs.azure.account.key.imec.blob.core.windows.net":"IUF5U0VO8Fd/X9IqM7o5Rys63kSBJaTlnCDDLtL6xbFN4OA/Fj3Q6S4LwvzCNlFi6K89JuvWaJBV+AStpqCErA=="})

File /databricks/python_shell/dbruntime/dbutils.py:362, in DBUtils.FSHandler.prettify_exception_message.<locals>.f_with_exception_handling(*args, **kwargs)
    360 exc.__context__ = None
    361 exc.__cause__ = None
--> 362 raise exc

ExecutionError: An error occurred while calling o3175.mount.
: java.rmi.RemoteException: java.lang.IllegalArgumentException: requirement failed: Directory already mounted: /mnt/imec; nested exception is: 
	java.lang.IllegalArgumentException: requirement failed: Directory already mo

In [0]:
import pickle
import numpy as np
import pandas as pd

In [0]:
#path for dataset
data_set = '/dbfs/mnt/imec/WESAD/'
# List of subject IDs
ids = ['S2','S3','S4','S5','S6','S7','S8','S9','S10','S11','S13','S14','S15','S16','S17']
numpy_df = []
# Function to preprocess the data for a given subject ID
def data_preprocess(i):
    # Construct the path for the subject's data
    path = data_set +i+'/'+i+'.pkl'
    with open(path, 'rb') as file:
        # Load data from the pickle file
        data = pickle.load(file, encoding='latin1')
    # Extract relevant signals from the data
    chest_a1=data['signal']['chest']['ACC'][0:,0]
    chest_a2=data['signal']['chest']['ACC'][0:,1]
    chest_a3=data['signal']['chest']['ACC'][0:,2]
    chest_ecg=data['signal']['chest']['ECG'][:,0]
    chest_emg=data['signal']['chest']['EMG'][:,0]
    chest_eda=data['signal']['chest']['EDA'][:,0]
    chest_temp=data['signal']['chest']['Temp'][:,0]
    chest_resp=data['signal']['chest']['Resp'][:,0]
    wrist_a1=data['signal']['wrist']['ACC'][0:,0]
    wrist_a2=data['signal']['wrist']['ACC'][0:,1]
    wrist_a3=data['signal']['wrist']['ACC'][0:,2]
    wrist_bvp=data['signal']['wrist']['BVP'][:,0]
    wrist_eda=data['signal']['wrist']['EDA'][:,0]
    wrist_temp=data['signal']['wrist']['TEMP'][:,0]
    wrist_label=data['label']
    # Create a numpy array from the extracted signals
    numpy_data1=np.array([chest_a1, chest_a2, chest_a3,chest_ecg,chest_emg,chest_eda,chest_temp,chest_resp,wrist_label])
    numpy_data1=numpy_data1.T
    # Create a DataFrame from the numpy array and add subject ID
    df = pd.DataFrame(data=numpy_data1, columns=["chest_a1", "chest_a2", "chest_a3","c_ecg","chest_emg","chest_eda","chest_temp","chest_resp","wrist_label"])
    df['Subject_id'] = i
    # Calculate quartiles and interquartile range
    Qquantile1 = df.quantile(0.25)
    Qquantile3 = df.quantile(0.75)
    Inter_Qqantile_Range = Qquantile3 - Qquantile1
    df_outliners = df[~((df < (Qquantile1 - 1.5 * Inter_Qqantile_Range)) |(df > (Qquantile3 + 1.5 * Inter_Qqantile_Range))).any(axis=1)]
    # Filter outliers using interquartile range
    norm_df_out=(df_outliners-df_outliners.mean())/df_outliners.std()
    norm_df_out['Subject_id'] = i
    return norm_df_out


In [0]:
df = data_preprocess("S2")

<command-4150418451625903>:39: FutureWarning: Automatic reindexing on DataFrame vs Series comparisons is deprecated and will raise ValueError in a future version. Do `left, right = left.align(right, axis=1, copy=False)` before e.g. `left == right`
  df_outliners = df[~((df < (Qquantile1 - 1.5 * Inter_Qqantile_Range)) |(df > (Qquantile3 + 1.5 * Inter_Qqantile_Range))).any(axis=1)]
<command-4150418451625903>:41: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  norm_df_out=(df_outliners-df_outliners.mean())/df_outliners.std()
<command-4150418451625903>:41: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  norm_df_out=(df_outliners-df_outliners.mean())/df_outline

In [0]:
display(df)

Subject_id c_ecg chest_a1 chest_a2 chest_a3 chest_eda chest_emg chest_resp chest_temp wrist_label S2 -0.32625869033147203 -1.678430209367321 2.2512208892715493 -1.593855821698935 3.5634824255586333 -0.6755946719741328 -0.4167527678428661 -4.750996364339048 -0.10896154781248622 S2 -1.9133464116311107 -1.6979915172969862 2.1162802214828207 -1.5640928456097856 3.5539010361208407 -1.408406312033566 0.864868650720598 -4.753545504444825 -0.10896154781248622 S2 0.8434062368164921 -1.7104395259843874 2.2441196400686696 -1.574550042685973 3.5870003814513973 1.3024843004939877 -0.7317275232525309 -4.748553438404345 -0.10896154781248622 S2 -1.4524191310177181 -1.7460049622494644 1.9529282070323175 -1.6067266606862425 3.5861293460479615 0.22120278963706178 1.1214644643948508 -4.753545504444825 -0.10896154781248622 S2 0.7663096785299031 -1.7122181157815146 2.158891949933602 -1.596269223876055 3.5539010361208407 -0.5372316350398342 0.9497217637081155 -4.571494415223894 -0.10896154781248622 S2 0.37091447246011106 -1.7104395259843874 1.9884408028969716 -1.5858117870658675 3.2525227865320883 0.2570746881015095 -0.4167527678428661 -4.743561372363864 -0.10896154781248622 S2 0.3918406811378995 -1.6730954999221836 2.038155897167385 -1.5640928456097856 3.2255206890255814 -0.45011416734046106 -0.38077504793615863 -4.753545504444825 -0.10896154781248622 S2 0.6385496676549842 -1.678430209367321 2.0594617613927757 -1.5914426592558146 3.2481676095149097 -0.2758792319417146 -0.5925684179530022 -4.748553438404345 -0.10896154781248622 S2 0.6231303559976664 -1.7033262267421234 2.0452571463702647 -1.5729411878125596 3.220294476604967 -0.3783703704115654 0.1120518322953429 -4.733577240282903 -0.10896154781248622 S2 -2.2801057531944555 -1.6926568078518491 2.201505795001136 -1.6099443704330694 3.1993896269225104 -0.04014961346105778 -0.5226494528512878 -4.733577240282903 -0.10896154781248622 S2 1.2966238616012258 -1.6535341919925184 2.087870991437798 -1.5825940773190406 3.1906792728881532 -0.06064784115502794 -0.5728824957398981 -4.721097075181701 -0.10896154781248622 S2 0.27289170549573366 -1.6357514738599799 1.9742361878744603 -1.5793763675722137 3.247296574111474 -1.9259865613063125 -0.5491236241033933 -4.71111294310074 -0.10896154781248622 S2 -1.8054112300298861 -1.7068834063363774 1.8606013843111224 -1.6163795501927234 3.2229075828152745 -1.029189099695118 -0.266053639177035 -4.7311343143482 -0.10896154781248622 S2 2.361107055658201 -1.7104395259843874 1.8037829242210777 -1.5970735314457618 3.218552405798096 2.511879734438227 0.9341087909184123 -4.7311343143482 -0.10896154781248622 S2 0.886360033576163 -1.685543508609585 1.8748059993336337 -1.5954649163063481 3.1697744232056966 1.0360073404723755 0.8974522461078047 -4.738569306323384 -0.10896154781248622 S2 1.1936448873184247 -1.6713169101250567 2.1730965649561136 -1.6067266606862425 3.218552405798096 0.1904554480961065 -0.309498433026644 -4.721097075181701 -0.10896154781248622 S2 1.0768986704844472 -1.678430209367321 2.016847916325242 -1.5986826260531752 3.1593219983644683 -0.2758792319417146 -0.5145035540044861 -4.750996364339048 -0.10896154781248622 S2 0.5504393153274539 -1.6748740897193106 1.9742361878744603 -1.5906383516861078 3.1575799275575966 -0.00427771499661 -0.43032926592086884 -4.718654149246998 -0.10896154781248622 S2 -0.7392759668667701 -1.7068834063363774 2.0736663764152867 -1.6139661480156033 3.2716855654076733 -1.3007906166402228 0.2328826651895678 -4.733577240282903 -0.10896154781248622 S2 0.44305482342827646 -1.7673448599762567 1.9529282070323175 -1.5890294968126943 3.1636771753816464 0.08796430962625572 0.6619000044544563 -4.723593108201942 -0.10896154781248622 S2 0.5052827597595947 -1.7886847577030491 1.8108862900407092 -1.5496133914830643 3.1445143965060613 -1.341787072028163 1.0800561452569424 -4.723593108201942 -0.10896154781248622 S2 -2.2074147125242427 -1.649978072344508 1.0509510277284946 -1.6163795501927234 3.138417148682011 0.03671874039133032 1.3658414297989012 -4.723593108201